<a href="https://colab.research.google.com/github/Dahyun1016/healthy_wealthy/blob/main/AI/image_download_py.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import requests
import os

In [2]:
# 이미지 저장 디렉토리 설정
image_dir = "drug_images"
if not os.path.exists(image_dir):
    os.makedirs(image_dir)

In [3]:
import pandas as pd
import requests
import os

In [5]:
# CSV 파일 불러오기
file_path = '/content/OpenData_PotOpenTabletIdntfcC20240827.csv'  # CSV 파일 경로
df = pd.read_csv(file_path)

In [6]:
# 데이터 확인
df.head()  # 첫 몇 줄을 출력하여 데이터를 확인

품목일련번호                      품목명    업소일련번호      업소명                  성상  \
0  200808876  가스디알정50밀리그램(디메크로틴산마그네슘)  19540006  일동제약(주)          녹색의원형필름코팅정   
1  200808877       페라트라정2.5밀리그램(레트로졸)  19560004  (주)유한양행       어두운황색의원형필름코팅정   
2  200808948         졸뎀속붕정(졸피뎀타르타르산염)  20080422  보령제약(주)         흰색의원형구강붕해정제   
3  200809076    가스프렌정(모사프리드시트르산염이수화물)  19760002  경동제약(주)  분할선을가진흰색의장방형필름코팅정제   
4  200809361               바르탄정(발사르탄)  19870002   (주)휴온스        엷은적색의원형필름코팅정   

                                              큰제품이미지    표시앞  표시뒤 의약품제형 색상앞  \
0  https://nedrug.mfds.go.kr/pbp/cmn/itemImageDow...    IDG    -    원형  연두   
1  https://nedrug.mfds.go.kr/pbp/cmn/itemImageDow...     YH   LT    원형  노랑   
2  https://nedrug.mfds.go.kr/pbp/cmn/itemImageDow...      -    -    원형  하양   
3  https://nedrug.mfds.go.kr/pbp/cmn/itemImageDow...     KD  분할선   장방형  하양   
4  https://nedrug.mfds.go.kr/pbp/cmn/itemImageDow...  V분할선T  HS8    원형  분홍   

   ...  제형코드명 표기내용앞 표기내용뒤 표기이미지앞 표기이미지뒤 표기코드앞  표기코드뒤      변경일자       사업자번호  \
0  ...    당의정     -     -      -      -     -      -         -  6828500435   
1  ...  필름코팅정     -     -      -      -     -      -         -  1188100601   
2  ...     정제     -     -      -      -     -      -         -  1348502031   
3  ...  필름코팅정     -     -      -      -     -      -  20211223  1248135518   
4  ...  필름코팅정     -     -      -      -     -      -         -  8638700270   

  Unnamed: 30  
0         NaN  
1         NaN  
2         NaN  
3         NaN  
4         NaN  

[5 rows x 31 columns]

In [7]:
from google.colab import drive

# 구글 드라이브 마운트
drive.mount('/content/drive')

Mounted at /content/drive


In [8]:
import time
import pandas as pd
import urllib.request as req
from tqdm import tqdm
import os
from concurrent.futures import ThreadPoolExecutor
from google.colab import drive

# 구글 드라이브 마운트
drive.mount('/content/drive')

# 오류 로그와 중복 로그를 위한 리스트 초기화
error_log = []
skip_log = []

def download_image(image_url, image_path):
    try:
        req.urlretrieve(image_url, image_path)
        return f"{image_path} 다운로드 완료"
    except Exception as e:
        # 오류가 발생할 경우 로그에 추가
        error_log.append((image_url, str(e)))
        return f"{image_path} 다운로드 중 오류 발생: {e}"

def download(excel_file_name, data_save_dir):
    # 파일 확장자에 따라 파일 읽기
    if excel_file_name.split(".")[-1] == "xls":
        df = pd.read_excel(excel_file_name, engine="openpyxl")
    elif excel_file_name.split(".")[-1] == "csv":
        df = pd.read_csv(excel_file_name)

    # 저장할 디렉토리 생성
    os.makedirs(data_save_dir, exist_ok=True)

    start = time.time()

    # max_workers 값 조정으로 병렬 다운로드 최대화 (네트워크 상황에 따라 조정 가능)
    with ThreadPoolExecutor(max_workers=20) as executor:  # 병렬 다운로드 설정
        futures = []
        with tqdm(total=len(df)) as pbar:  # tqdm으로 전체 진행 상황 표시
            for idx in range(len(df)):
                item_name = str(df["품목명"].iloc[idx]).replace('/', '_').replace('\\', '_').replace(' ', '_')
                image_url = df["큰제품이미지"].iloc[idx]
                image_path = os.path.join(data_save_dir, f"{item_name}.jpg")

                # 이미 파일이 존재하는 경우 건너뛰기 및 로그 기록
                if os.path.exists(image_path):
                    skip_log.append(f"{image_path} 중복되어 건너뛰었습니다.")
                    pbar.update(1)  # 건너뛴 항목도 진행 바에 반영
                    continue

                futures.append(executor.submit(download_image, image_url, image_path))

            # 다운로드 완료 후 결과 확인
            for future in futures:
                result = future.result()
                print(result)
                pbar.update(1)

    print("총 소요 시간:", time.time() - start)

    # 오류 로그 출력
    if error_log:
        print("\n다운로드 중 오류가 발생한 항목들:")
        for url, error in error_log:
            print(f"URL: {url} - Error: {error}")
    else:
        print("\n모든 이미지가 성공적으로 다운로드되었습니다.")

    # 중복 로그 출력
    if skip_log:
        print("\n중복된 항목들:")
        for skipped in skip_log:
            print(skipped)

# 구글 드라이브 내 저장할 디렉토리 설정 (구글 드라이브 내 경로)
data_save_dir = "/content/drive/My Drive/drug_images"

# CSV 파일 경로 설정
excel_file_name = "/content/OpenData_PotOpenTabletIdntfcC20240827.csv"  # 실제 파일 경로로 변경

# 다운로드 함수 호출
download(excel_file_name, data_save_dir)

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


  0%|          | 1/25445 [00:06<48:34:28,  6.87s/it]

/content/drive/My Drive/drug_images/가스디알정50밀리그램(디메크로틴산마그네슘).jpg 다운로드 완료
/content/drive/My Drive/drug_images/페라트라정2.5밀리그램(레트로졸).jpg 다운로드 완료
/content/drive/My Drive/drug_images/졸뎀속붕정(졸피뎀타르타르산염).jpg 다운로드 완료
/content/drive/My Drive/drug_images/가스프렌정(모사프리드시트르산염이수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/바르탄정(발사르탄).jpg 다운로드 완료
/content/drive/My Drive/drug_images/리피논정80밀리그램(아토르바스타틴칼슘삼수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/사르발탄정160밀리그램(발사르탄).jpg 다운로드 완료
/content/drive/My Drive/drug_images/가스베트정5밀리그램(모사프리드시트르산염수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/아푸르탄정150밀리그램(이르베사르탄).jpg 다운로드 완료
/content/drive/My Drive/drug_images/발사르텔정80밀리그램(발사르탄).jpg 다운로드 완료
/content/drive/My Drive/drug_images/발사르텔정160밀리그램(발사르탄).jpg 다운로드 완료
/content/drive/My Drive/drug_images/에스시탈정5밀리그램(에스시탈로프람옥살산염).jpg 다운로드 완료


  0%|          | 13/25445 [00:07<3:06:36,  2.27it/s]

/content/drive/My Drive/drug_images/발산정80밀리그램(발사르탄).jpg 다운로드 완료
/content/drive/My Drive/drug_images/가스리드정5mg(모사프리드시트르산염수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/엑스반정80밀리그램(발사르탄).jpg 다운로드 완료
/content/drive/My Drive/drug_images/뉴멘타민서방캡슐8밀리그램(갈란타민브롬화수소산염).jpg 다운로드 완료
/content/drive/My Drive/drug_images/발트렙정160밀리그램(발사르탄).jpg 다운로드 완료
/content/drive/My Drive/drug_images/수로신디정(탐스로신염산염).jpg 다운로드 완료
/content/drive/My Drive/drug_images/로수로드정10밀리그램(로수바스타틴칼슘).jpg 다운로드 완료
/content/drive/My Drive/drug_images/디오살탄정160밀리그램(발사르탄).jpg 다운로드 완료
/content/drive/My Drive/drug_images/디오살탄정80밀리그램(발사르탄).jpg 다운로드 완료
/content/drive/My Drive/drug_images/칸데사르정8밀리그램(칸데사르탄실렉세틸).jpg 다운로드 완료
/content/drive/My Drive/drug_images/칸데사르정16밀리그램(칸데사르탄실렉세틸).jpg 다운로드 완료
/content/drive/My Drive/drug_images/디로탄정160mg(발사르탄).jpg 다운로드 완료
/content/drive/My Drive/drug_images/인케어정(옥수수불검화정량추출물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/제이코정.jpg 다운로드 완료
/content/drive/My Drive/drug_images/깅코탄연질캡슐120밀리그램(은행엽건조엑스).jpg 다운로드

...

/content/drive/My Drive/drug_images/몬테라젠정10_5밀리그램(몬테루카스트|레보세티리진).jpg 다운로드 완료
/content/drive/My Drive/drug_images/피오시타정100_30밀리그램(시타글립틴인산염수화물|피오글리타존염산염).jpg 다운로드 완료
/content/drive/My Drive/drug_images/로우로제정10_2.5밀리그램(에제티미브|로수바스타틴칼슘).jpg 다운로드 완료
/content/drive/My Drive/drug_images/페바로젯정2_10밀리그램.jpg 다운로드 완료
/content/drive/My Drive/drug_images/에이시타정25밀리그램(시타글립틴염산염수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/에이시타정100밀리그램(시타글립틴염산염수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/에이시타정50밀리그램(시타글립틴염산염수화물).jpg 다운로드 완료


100%|█████████▉| 25430/25445 [1:00:33<00:01, 12.40it/s]

/content/drive/My Drive/drug_images/시다프비아정10_100밀리그램(다파글리플로진|시타글립틴).jpg 다운로드 완료
/content/drive/My Drive/drug_images/징코더블에스정240밀리그램(은행엽건조엑스).jpg 다운로드 완료
/content/drive/My Drive/drug_images/제이더블유중외제약도네페질정5밀리그램(도네페질염산염수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/시타칸메트서방정50_500밀리그램.jpg 다운로드 완료
/content/drive/My Drive/drug_images/시타칸메트서방정50_1000밀리그램.jpg 다운로드 완료
/content/drive/My Drive/drug_images/시타칸메트서방정100_1000밀리그램.jpg 다운로드 완료
/content/drive/My Drive/drug_images/시타칸다플정10_100밀리그램.jpg 다운로드 완료


100%|██████████| 25445/25445 [1:00:36<00:00,  7.00it/s]

/content/drive/My Drive/drug_images/시글립정25밀리그램(시타글립틴염산염수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/리스달정0.5밀리그램(리스페리돈).jpg 다운로드 완료
/content/drive/My Drive/drug_images/아도르정40밀리그램(아토르바스타틴칼슘수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/테미스타정80_5밀리그램.jpg 다운로드 완료
/content/drive/My Drive/drug_images/당이자누정25밀리그램(시타글립틴염산염수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/당이자누정50밀리그램(시타글립틴염산염수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/시타렌정25밀리그램(시타글립틴염산염수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/다포가플러스정10_100밀리그램.jpg 다운로드 완료
/content/drive/My Drive/drug_images/자누글루엠정50_500밀리그램(시타글립틴염산염수화물_메트포르민염산염).jpg 다운로드 완료
/content/drive/My Drive/drug_images/자누글루엠정50_850밀리그램(시타글립틴염산염수화물_메트포르민염산염).jpg 다운로드 완료
/content/drive/My Drive/drug_images/자누글루엠정50_1000밀리그램(시타글립틴염산염수화물_메트포르민염산염).jpg 다운로드 완료
/content/drive/My Drive/drug_images/자누글루정100밀리그램(시타글립틴염산염수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_images/자누글루정50밀리그램(시타글립틴염산염수화물).jpg 다운로드 완료
/content/drive/My Drive/drug_imag